In [ ]:
# pip install colorcet

In [2]:
import folium
import matplotlib
import colorcet
from matplotlib.pyplot import imread
from matplotlib.colors import Normalize
from folium import raster_layers

In [3]:
image = '/notebooks/resources/gpm/gpm_1d.20190531.tif'

In [4]:
from osgeo import gdal,ogr,osr

def GetExtent(gt,cols,rows):
    ''' Return list of corner coordinates from a geotransform

        @type gt:   C{tuple/list}
        @param gt: geotransform
        @type cols:   C{int}
        @param cols: number of columns in the dataset
        @type rows:   C{int}
        @param rows: number of rows in the dataset
        @rtype:    C{[float,...,float]}
        @return:   coordinates of each corner
    '''
    ext=[]
    xarr=[0,cols]
    yarr=[0,rows]

    for px in xarr:
        for py in yarr:
            x=gt[0]+(px*gt[1])+(py*gt[2])
            y=gt[3]+(px*gt[4])+(py*gt[5])
            ext.append([y,x])
            print (y,x)
        yarr.reverse()
    return ext

def ReprojectCoords(coords,src_srs,tgt_srs):
    ''' Reproject a list of x,y coordinates.

        @type geom:     C{tuple/list}
        @param geom:    List of [[x,y],...[x,y]] coordinates
        @type src_srs:  C{osr.SpatialReference}
        @param src_srs: OSR SpatialReference object
        @type tgt_srs:  C{osr.SpatialReference}
        @param tgt_srs: OSR SpatialReference object
        @rtype:         C{tuple/list}
        @return:        List of transformed [[x,y],...[x,y]] coordinates
    '''
    trans_coords=[]
    transform = osr.CoordinateTransformation( src_srs, tgt_srs)
    for x,y in coords:
        x,y,z = transform.TransformPoint(x,y)
        trans_coords.append([x,y])
    return trans_coords

raster=image
ds=gdal.Open(raster)

gt=ds.GetGeoTransform()
cols = ds.RasterXSize
rows = ds.RasterYSize

ext=GetExtent(gt,cols,rows)
print("ext = " + str(ext))

src_srs=osr.SpatialReference()
src_srs.ImportFromWkt(ds.GetProjection())
# tgt_srs=osr.SpatialReference()
# tgt_srs.ImportFromEPSG(3857)
tgt_srs = src_srs.CloneGeogCS()

geo_ext=ReprojectCoords(ext,src_srs,tgt_srs)
print("geo_ext = " + str(geo_ext))

10.0 -180.0
-60.0 -180.0
-60.0 -30.0
10.0 -30.0
ext = [[10.0, -180.0], [-60.0, -180.0], [-60.0, -30.0], [10.0, -30.0]]
geo_ext = [[10.0, -180.0], [-60.0, -180.0], [-60.0, -30.0], [10.0, -30.0]]


In [5]:
!gdalinfo '/notebooks/resources/gpm/gpm_1d.20190531.tif'

Driver: GTiff/GeoTIFF
Files: /notebooks/resources/gpm/gpm_1d.20190531.tif
Size is 1500, 700
Coordinate System is:
GEOGCS["WGS 84",
    DATUM["WGS_1984",
        SPHEROID["WGS 84",6378137,298.2572326660159,
            AUTHORITY["EPSG","7030"]],
        AUTHORITY["EPSG","6326"]],
    PRIMEM["Greenwich",0],
    UNIT["degree",0.0174532925199433],
    AUTHORITY["EPSG","4326"]]
Origin = (-180.000000000000000,10.000000000000000)
Pixel Size = (0.100000000000000,-0.100000000000000)
Metadata:
  AREA_OR_POINT=Area
  TIFFTAG_DATETIME=2019:06:01 13:35:13
  TIFFTAG_DOCUMENTNAME=/NRTPUB/imerg/gis/2019/05/3B-HHR-L.MS.MRG.3IMERG.20190531-S233000-E235959.1410.V06B.1day.tif
  TIFFTAG_IMAGEDESCRIPTION=DOI=10.5067/GPM/IMERG/3B-HH-L/06 DOIauthority=http://dx.doi.org/ DOIshortName=3IMERGHH_LATE Unit=0.1(mm) ScaleFactor=10
  TIFFTAG_RESOLUTIONUNIT=2 (pixels/inch)
  TIFFTAG_SOFTWARE=IDL 8.7.2, Harris Geospatial Solutions, Inc.
  TIFFTAG_XRESOLUTION=100
  TIFFTAG_YRESOLUTION=100
Image Structure Metadata:
  COM

In [6]:
!gdal_edit -colorinterp_1 alpha /notebooks/resources/gpm/gpm_1d.20190531.tif

/bin/sh: 1: gdal_edit: not found


In [10]:
m = folium.Map(
      location = [-22, -114]
    , zoom_start = 2
    , control_scale = True 
    , tiles = 'Stamen Terrain'
)

data = matplotlib.pyplot.imread(image)

# Image bounds on the map in the form
# [[lat_min, lon_min], [lat_max, lon_max]]
m.add_child(raster_layers.ImageOverlay(
      data
    , opacity = 0.7
    , bounds = [ext[2], ext[0]]
    , mercator_project = True
#     , colormap = lambda x: (1, 0, 0, x)
    , colormap = colorcet.cm.bmw
)
           )

folium.Marker(
      ext[2]
    , popup = str(ext[2])
    , tooltip = str(ext[2])
).add_to(m)

folium.Marker(
      ext[0]
    , popup = str(ext[0])
    , tooltip = str(ext[0])
).add_to(m)

m

In [ ]:
vars(m)

In [ ]:
print(data)
print(data.shape)
# data = data.transpose()
# print(data)
# print(data.shape)

In [ ]:
# First: read the geotiff image with GDAL.
from osgeo import gdal, osr

gdal.UseExceptions()

ds = gdal.Open(image)
data = ds.ReadAsArray()
gt = ds.GetGeoTransform()
proj = ds.GetProjection()

inproj = osr.SpatialReference()
inproj.ImportFromWkt(proj)

print('\n\n## ds ##:\n\n' + str(ds))
print('\n\n## data ##:\n\n' + str(data))
print('\n\n## gt ##:\n\n' + str(gt))
print('\n\n## proj ##:\n\n' + str(proj))
print('\n\n## inproj ##:\n\n' + str(inproj))

In [ ]:
q = lambda x: (0, 0, 0, 0)
print(q(9))